<a href="https://colab.research.google.com/github/MK316/SpeechProcessing/blob/main/Pitch_manipulation.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Pitch manipulation

[Original tutorial](https://parselmouth.readthedocs.io/en/stable/examples/pitch_manipulation.html)

In [39]:
!pip install praat-parselmouth

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [40]:
import parselmouth
url = "/content/sample02.wav"
sound = parselmouth.Sound(url)

In [41]:
from IPython.display import Audio

Audio(data=sound.values, rate=sound.sampling_frequency)

"However, now we want to use the Praat Manipulation functionality, but unfortunately, Parselmouth does not yet contain a Manipulation class and the necessary functionality is not directly accessible through the Sound object sound. To directly access the Praat commands conveniently from Python, we can make use of the parselmouth.praat.call function." [source](https://parselmouth.readthedocs.io/en/stable/examples/pitch_manipulation.html)

In [42]:
from parselmouth.praat import call

manipulation = call(sound, "To Manipulation", 0.01, 75, 600)

In [43]:
type(manipulation)

parselmouth.Data

In [44]:
manipulation.class_name

'Manipulation'

In [45]:
pitch_tier = call(manipulation, "Extract pitch tier")

call(pitch_tier, "Multiply frequencies", sound.xmin, sound.xmax, 2)

call([pitch_tier, manipulation], "Replace pitch tier")
sound_octave_up = call(manipulation, "Get resynthesis (overlap-add)")

In [46]:
type(sound_octave_up)

parselmouth.Sound

In [47]:
Audio(data=sound_octave_up.values, rate=sound_octave_up.sampling_frequency)

Saving the file

In [48]:
sound_octave_up.save("4_b_octave_up.wav", "WAV")
Audio(filename="4_b_octave_up.wav")

In [49]:
# Clean up the created audio file again
# !rm 4_b_octave_up.wav

We can of course also turn this combination of commands into a custom function, to be reused in later code:

In [50]:
def change_pitch(sound, factor):
    manipulation = call(sound, "To Manipulation", 0.01, 75, 600)

    pitch_tier = call(manipulation, "Extract pitch tier")

    call(pitch_tier, "Multiply frequencies", sound.xmin, sound.xmax, factor)

    call([pitch_tier, manipulation], "Replace pitch tier")
    return call(manipulation, "Get resynthesis (overlap-add)")

Using Jupyter widgets, one can then change the audio file or the pitch change factor, and interactively hear how this sounds.

To try this for yourself, open an online, interactive version of this notebook on Binder! (see link at the top of this notebook)

In [55]:
import ipywidgets
import glob

def interactive_change_pitch(audio_file, factor):
    sound = parselmouth.Sound(audio_file)
    sound_changed_pitch = change_pitch(sound, factor)
    return Audio(data=sound_changed_pitch.values, rate=sound_changed_pitch.sampling_frequency)

In [60]:
print(sorted(glob.glob("audio/*.wav")))

['audio/4_b_octave_up.wav', 'audio/sample02.wav']


In [62]:
w = ipywidgets.interact(interactive_change_pitch,
                        audio_file=ipywidgets.Dropdown(options=sorted(glob.glob("audio/*.wav")), value="audio/4_b_octave_up.wav"),
                        factor=ipywidgets.FloatSlider(min=0.25, max=4, step=0.05, value=1.5))

interactive(children=(Dropdown(description='audio_file', options=('audio/4_b_octave_up.wav', 'audio/sample02.w…